In [5]:
import numpy as np
import pygad
import time

# Schwefel function
def schwefel_function(solution):
    return 418.9829 * len(solution) - sum([x * np.sin(np.sqrt(abs(x))) for x in solution])

# Fitness function for optimization
def fitness_function(ga_instance, solution, solution_idx):
    return -schwefel_function(solution)  # For minimization, we return the negative value

# Variables to track best solution and iteration details
best_fitness = float('inf')
best_generation = 0
best_time = 0

start_time = time.time()

# Callback function called after each generation
def on_generation(ga_instance):
    global best_fitness, best_generation, best_time
    current_best_fitness = ga_instance.best_solution()[1]

    # If a better solution is found, update tracking variables
    if current_best_fitness < best_fitness:
        best_fitness = current_best_fitness
        best_generation = ga_instance.generations_completed
        best_time = time.time() - start_time  # Time elapsed since the start

    print(f"Iteration: {ga_instance.generations_completed}, "
          f"Best Fitness: {-ga_instance.best_solution()[1]:.6f}")

# Define parameter ranges (updated for Schwefel)
param_ranges = {
    "x0": (-500, 500),
    "x1": (-500, 500),
    "x2": (-500, 500),
    "x3": (-500, 500),
    "x4": (-500, 500),
    "x5": (-500, 500),
    "x6": (-500, 500),
    "x7": (-500, 500),
    "x8": (-500, 500),
    "x9": (-500, 500),
}

num_generations = 100  # Number of generations
num_parents_mating = 100  # Number of parents mating per generation
sol_per_pop = 500  # Population size

# Generate initial population based on parameter ranges
initial_population = np.array([
    [np.random.uniform(param_ranges[param][0], param_ranges[param][1]) for param in param_ranges]
    for _ in range(sol_per_pop)
])

# Setup the genetic algorithm
ga_instance = pygad.GA(
    num_generations=num_generations,
    num_parents_mating=num_parents_mating,
    fitness_func=fitness_function,
    sol_per_pop=sol_per_pop,
    num_genes=len(param_ranges),
    init_range_low=-500,
    init_range_high=500,
    mutation_percent_genes=20,  # Mutation rate
    crossover_type="single_point",  # Crossover type
    mutation_type="random",  # Mutation type
    mutation_by_replacement=True,
    mutation_num_genes=int(0.1 * len(param_ranges)),  # Number of genes mutating
    random_mutation_min_val=-500,
    random_mutation_max_val=500,
    initial_population=initial_population,
    on_generation=on_generation  # Setting the callback function
)

# Run the genetic algorithm
ga_instance.run()

# Retrieve the best solution
best_solution, best_solution_fitness, _ = ga_instance.best_solution()

# Print the results
print(f"\nBest parameters: {best_solution}")
print(f"Schwefel function value: {-best_solution_fitness:.6f}")
print(f"Best iteration: {best_generation}, Time: {best_time:.2f} seconds")

Iteration: 1, Best Fitness: 1972.166144
Iteration: 2, Best Fitness: 1461.181077
Iteration: 3, Best Fitness: 1056.258435
Iteration: 4, Best Fitness: 945.258166
Iteration: 5, Best Fitness: 598.792980
Iteration: 6, Best Fitness: 598.792980
Iteration: 7, Best Fitness: 434.643182
Iteration: 8, Best Fitness: 356.737691
Iteration: 9, Best Fitness: 293.262426
Iteration: 10, Best Fitness: 293.262426
Iteration: 11, Best Fitness: 245.371290
Iteration: 12, Best Fitness: 245.371290
Iteration: 13, Best Fitness: 188.494431
Iteration: 14, Best Fitness: 134.553209
Iteration: 15, Best Fitness: 134.553209
Iteration: 16, Best Fitness: 134.553209
Iteration: 17, Best Fitness: 134.553209
Iteration: 18, Best Fitness: 134.553209
Iteration: 19, Best Fitness: 114.815456
Iteration: 20, Best Fitness: 114.815456
Iteration: 21, Best Fitness: 114.815456
Iteration: 22, Best Fitness: 99.060792
Iteration: 23, Best Fitness: 95.821731
Iteration: 24, Best Fitness: 95.821731
Iteration: 25, Best Fitness: 95.821731
Iteration:

In [9]:
import numpy as np
import pygad
import time
import pandas as pd
import random
from scipy import stats
import gc  # Для очистки памяти
from tqdm import tqdm  # Для отображения прогресса

# Функция Швефеля
def schwefel_function(solution):
    A = 418.9829 * len(solution)
    return A - sum([x * np.sin(np.sqrt(abs(x))) for x in solution])

# Определение целевой функции для оптимизации
def fitness_function(ga_instance, solution, solution_idx):
    return -schwefel_function(solution)  # Для минимизации используем отрицание

# Функция обратного вызова, которая вызывается после каждой итерации
def on_generation(ga_instance):
    current_best_fitness = -ga_instance.best_solution()[1]
    current_generation = ga_instance.generations_completed
    current_time = time.time() - start_time  # Время на текущую итерацию

    # Сохранение данных текущей итерации
    iterations_data.append({
        'generation': current_generation,
        'best_fitness': current_best_fitness,
        'time': current_time,
        'solution': ga_instance.best_solution()[0]  # Сохранение лучшего решения
    })

    print(f"Итерация: {current_generation}, Лучшая пригодность: {current_best_fitness:.6f}, Время на текущую итерацию: {current_time:.2f} секунд")

# Генерация случайных гиперпараметров (один раз в начале)
def generate_random_hyperparameters():
    hyperparameters = {
        "num_parents_mating": random.randint(2, 450),  # От 2 до 400
        "sol_per_pop": random.randint(100, 500),  # Размер популяции от 50 до 500
        "mutation_percent_genes": random.uniform(1, 50),  # Процент генов для мутации
        "mutation_num_genes": random.randint(1, 5),  # Количество генов для мутации
        "crossover_type": random.choice(["single_point", "two_points", "uniform", "scattered"]),  # Тип кроссинговера
        "mutation_type": random.choice(["random", "adaptive", "swap", "scramble", "inversion"]),  # Тип мутации
        "mutation_by_replacement": random.choice([True, False]),  # Замена генов
        "random_mutation_min_val": random.uniform(-10, 0),  # Мин. значение мутации
        "random_mutation_max_val": random.uniform(0, 10),  # Макс. значение мутации
        "keep_parents": random.uniform(0, 1),  # Процент родителей, сохраняемых для следующего поколения
        "num_genes": random.randint(5, 30)  # Длина решения для функции Швефеля (от 5 до 30 генов)
    }

    # Гарантируем, что количество родителей для скрещивания меньше или равно числу особей в популяции
    hyperparameters["num_parents_mating"] = min(hyperparameters["num_parents_mating"], hyperparameters["sol_per_pop"])

    # Для адаптивной мутации mutation_num_genes должен быть массивом из двух элементов
    if hyperparameters["mutation_type"] == "adaptive":
        hyperparameters["mutation_num_genes"] = np.random.randint(1, 5, size=2)  # Два целых числа
    else:
        hyperparameters["mutation_num_genes"] = hyperparameters["mutation_num_genes"]
    
    return hyperparameters

# Количество внешних прогонов с разными гиперпараметрами
num_outer_runs = 30

# Количество прогонов для каждого набора гиперпараметров
num_inner_runs = 30

# Массив для хранения суммарных результатов по каждому внешнему прогону
summary_results = []

# Внешний цикл для разных гиперпараметров с отображением прогресса
for outer_run in tqdm(range(num_outer_runs), desc="Outer Runs Progress"):
    print(f"\n=== Внешний прогон {outer_run + 1} с новыми гиперпараметрами ===\n")
    
    # Инициализируем гиперпараметры один раз перед внешним прогоном
    hyperparams = generate_random_hyperparameters()

    # Массив для хранения результатов по каждому внутреннему прогону
    results = []

    # Внутренний цикл для одного набора гиперпараметров
    for run in range(num_inner_runs):
        print(f"\n=== Внутренний прогон {run + 1} ===\n")

        # Очистка данных по итерациям для каждого внутреннего прогона
        iterations_data = []

        # Генерация начальной популяции с учётом диапазонов для функции Швефеля
        initial_population = np.array([
            [np.random.uniform(-500, 500) for _ in range(hyperparams["num_genes"])]  # Длина решения варьируется
            for _ in range(hyperparams["sol_per_pop"])])
        
        # Настройка генетического алгоритма с одними и теми же гиперпараметрами для всех прогонов
        ga_instance = pygad.GA(
            num_generations=100,  # Используем фиксированное количество поколений
            num_parents_mating=hyperparams["num_parents_mating"],
            fitness_func=fitness_function,
            sol_per_pop=hyperparams["sol_per_pop"],
            num_genes=hyperparams["num_genes"],  # Длина решения варьируется
            init_range_low=-500,
            init_range_high=500,
            mutation_percent_genes=hyperparams["mutation_percent_genes"],
            crossover_type=hyperparams["crossover_type"],
            mutation_type=hyperparams["mutation_type"],
            mutation_by_replacement=hyperparams["mutation_by_replacement"],
            mutation_num_genes=hyperparams["mutation_num_genes"] if hyperparams["mutation_type"] != "adaptive" else hyperparams["mutation_num_genes"],  # Массив для adaptive
            random_mutation_min_val=hyperparams["random_mutation_min_val"],
            random_mutation_max_val=hyperparams["random_mutation_max_val"],
            initial_population=initial_population,
            on_generation=on_generation  # Установка обратного вызова
        )

        # Запуск оптимизации
        start_time = time.time()
        ga_instance.run()

        # Поиск лучших итераций
        best_iterations = [d for d in iterations_data if d['best_fitness'] == min([data['best_fitness'] for data in iterations_data])]
        best_iteration = min(best_iterations, key=lambda x: x['time'])

        # Пересчёт функции Швефеля для лучших параметров
        best_solution_fitness = schwefel_function(best_iteration['solution'])

        # Сохранение результатов для текущего внутреннего прогона
        run_data = {
            'Значение функции Швефеля': best_solution_fitness,
            'Лучшая итерация': best_iteration['generation'],
            'Время до лучшей итерации': best_iteration['time']
        }
        results.append(run_data)

        # Очистка данных после внутреннего прогона
        iterations_data.clear()  # Очищаем список данных об итерациях
        del ga_instance
        gc.collect()  # Явная очистка памяти после каждого внутреннего прогона

    # Создание таблицы с результатами для одного набора гиперпараметров
    df_results = pd.DataFrame(results)

    # Вычисление медианы для времени и значения функции, моды для лучшей итерации
    median_time = df_results['Время до лучшей итерации'].median()
    median_fitness = df_results['Значение функции Швефеля'].median()
    mode_iteration = stats.mode(df_results['Лучшая итерация'])[0][0]

    # Добавление строки с медианными значениями и гиперпараметрами в итоговую таблицу
    summary_row = {
        'Медиана значения функции Швефеля': median_fitness,
        'Мода лучшей итерации': mode_iteration,
        'Медиана времени до лучшей итерации': median_time
    }

    # Добавляем гиперпараметры как отдельные столбцы
    for param, value in hyperparams.items():
        summary_row[param] = value

    summary_results.append(summary_row)

    # Очистка неиспользуемых данных
    del df_results
    gc.collect()

# Создание итоговой таблицы с результатами всех внешних прогонов
df_summary = pd.DataFrame(summary_results)

# Вывод итоговой таблицы
print("\nИтоговая таблица с медианными значениями и гиперпараметрами:")
print(df_summary)


Outer Runs Progress:   0%|          | 0/30 [00:00<?, ?it/s]c:\Users\oftuadmin\AppData\Local\Programs\Python\Python311\Lib\site-packages\pygad\pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")



=== Внешний прогон 1 с новыми гиперпараметрами ===


=== Внутренний прогон 1 ===

Итерация: 1, Лучшая пригодность: 1720.781380, Время на текущую итерацию: 0.19 секунд
Итерация: 2, Лучшая пригодность: 1720.781380, Время на текущую итерацию: 0.39 секунд
Итерация: 3, Лучшая пригодность: 1455.847568, Время на текущую итерацию: 0.53 секунд
Итерация: 4, Лучшая пригодность: 1352.619308, Время на текущую итерацию: 0.64 секунд
Итерация: 5, Лучшая пригодность: 1069.700718, Время на текущую итерацию: 0.78 секунд
Итерация: 6, Лучшая пригодность: 754.415152, Время на текущую итерацию: 0.97 секунд
Итерация: 7, Лучшая пригодность: 559.738056, Время на текущую итерацию: 1.19 секунд
Итерация: 8, Лучшая пригодность: 194.396777, Время на текущую итерацию: 1.29 секунд
Итерация: 9, Лучшая пригодность: 194.396777, Время на текущую итерацию: 1.40 секунд
Итерация: 10, Лучшая пригодность: 66.088191, Время на текущую итерацию: 1.55 секунд
Итерация: 11, Лучшая пригодность: 52.594958, Время на текущую итерацию: 

C:\Users\oftuadmin\AppData\Local\Temp\ipykernel_9144\751647294.py:143: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode_iteration = stats.mode(df_results['Лучшая итерация'])[0][0]
Outer Runs Progress:   3%|▎         | 1/30 [02:55<1:24:57, 175.77s/it]c:\Users\oftuadmin\AppData\Local\Programs\Python\Python311\Lib\site-packages\pygad\pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter 


=== Внешний прогон 2 с новыми гиперпараметрами ===


=== Внутренний прогон 1 ===

Итерация: 1, Лучшая пригодность: 627.957654, Время на текущую итерацию: 0.03 секунд
Итерация: 2, Лучшая пригодность: 627.957654, Время на текущую итерацию: 0.10 секунд
Итерация: 3, Лучшая пригодность: 455.151899, Время на текущую итерацию: 0.15 секунд
Итерация: 4, Лучшая пригодность: 455.151899, Время на текущую итерацию: 0.24 секунд
Итерация: 5, Лучшая пригодность: 455.151899, Время на текущую итерацию: 0.31 секунд
Итерация: 6, Лучшая пригодность: 455.151899, Время на текущую итерацию: 0.36 секунд
Итерация: 7, Лучшая пригодность: 455.151899, Время на текущую итерацию: 0.41 секунд
Итерация: 8, Лучшая пригодность: 455.151899, Время на текущую итерацию: 0.44 секунд
Итерация: 9, Лучшая пригодность: 455.020080, Время на текущую итерацию: 0.47 секунд
Итерация: 10, Лучшая пригодность: 455.020080, Время на текущую итерацию: 0.50 секунд
Итерация: 11, Лучшая пригодность: 455.020080, Время на текущую итерацию: 0.5

C:\Users\oftuadmin\AppData\Local\Temp\ipykernel_9144\751647294.py:143: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode_iteration = stats.mode(df_results['Лучшая итерация'])[0][0]
Outer Runs Progress:   7%|▋         | 2/30 [05:12<1:11:18, 152.80s/it]c:\Users\oftuadmin\AppData\Local\Programs\Python\Python311\Lib\site-packages\pygad\pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter 

...


=== Внешний прогон 29 с новыми гиперпараметрами ===


=== Внутренний прогон 1 ===

Итерация: 1, Лучшая пригодность: 1333.128875, Время на текущую итерацию: 0.02 секунд
Итерация: 2, Лучшая пригодность: 1170.205610, Время на текущую итерацию: 0.05 секунд
Итерация: 3, Лучшая пригодность: 957.789577, Время на текущую итерацию: 0.08 секунд
Итерация: 4, Лучшая пригодность: 844.458059, Время на текущую итерацию: 0.14 секунд
Итерация: 5, Лучшая пригодность: 648.760766, Время на текущую итерацию: 0.21 секунд
Итерация: 6, Лучшая пригодность: 648.760766, Время на текущую итерацию: 0.29 секунд
Итерация: 7, Лучшая пригодность: 418.067824, Время на текущую итерацию: 0.40 секунд
Итерация: 8, Лучшая пригодность: 418.067824, Время на текущую итерацию: 0.46 секунд
Итерация: 9, Лучшая пригодность: 276.645619, Время на текущую итерацию: 0.53 секунд
Итерация: 10, Лучшая пригодность: 185.151876, Время на текущую итерацию: 0.63 секунд
Итерация: 11, Лучшая пригодность: 185.151876, Время на текущую итерацию: 

C:\Users\oftuadmin\AppData\Local\Temp\ipykernel_9144\751647294.py:143: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode_iteration = stats.mode(df_results['Лучшая итерация'])[0][0]
Outer Runs Progress:  97%|█████████▋| 29/30 [3:37:15<06:02, 362.74s/it]c:\Users\oftuadmin\AppData\Local\Programs\Python\Python311\Lib\site-packages\pygad\pygad.py:832: UserWarning: The mutation_by_replacement parameter is set to True while the mutation_type parameter is not set to random but (inversion). Note that the mutation_by_replacement parameter has an effect only when mutation_type='random'.
  warnings.warn(f"The mutation_by_replacement pa


=== Внешний прогон 30 с новыми гиперпараметрами ===


=== Внутренний прогон 1 ===

Итерация: 1, Лучшая пригодность: 6055.804394, Время на текущую итерацию: 0.12 секунд
Итерация: 2, Лучшая пригодность: 5433.921290, Время на текущую итерацию: 0.20 секунд
Итерация: 3, Лучшая пригодность: 5433.921290, Время на текущую итерацию: 0.28 секунд
Итерация: 4, Лучшая пригодность: 5433.921290, Время на текущую итерацию: 0.46 секунд
Итерация: 5, Лучшая пригодность: 5433.921290, Время на текущую итерацию: 0.56 секунд
Итерация: 6, Лучшая пригодность: 5433.921290, Время на текущую итерацию: 0.61 секунд
Итерация: 7, Лучшая пригодность: 5091.042886, Время на текущую итерацию: 0.64 секунд
Итерация: 8, Лучшая пригодность: 4953.770070, Время на текущую итерацию: 0.67 секунд
Итерация: 9, Лучшая пригодность: 4953.770070, Время на текущую итерацию: 0.70 секунд
Итерация: 10, Лучшая пригодность: 4524.377379, Время на текущую итерацию: 0.73 секунд
Итерация: 11, Лучшая пригодность: 4524.377379, Время на текущую и

C:\Users\oftuadmin\AppData\Local\Temp\ipykernel_9144\751647294.py:143: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode_iteration = stats.mode(df_results['Лучшая итерация'])[0][0]
Outer Runs Progress: 100%|██████████| 30/30 [3:39:47<00:00, 439.59s/it]


Итоговая таблица с медианными значениями и гиперпараметрами:
    Медиана значения функции Швефеля  Мода лучшей итерации   
0                           1.229439                    28  \
1                         430.269194                    66   
2                           2.005291                    31   
3                           8.578610                   100   
4                         511.542003                    94   
5                         807.976982                     1   
6                           0.281718                    25   
7                          15.181170                   100   
8                         484.410284                    53   
9                           2.233107                    26   
10                          6.727216                    63   
11                          0.034049                    98   
12                       5292.453229                    41   
13                       2152.396706                     1   
14      

In [10]:
df_summary

Медиана значения функции Швефеля  Мода лучшей итерации   
0                           1.229439                    28  \
1                         430.269194                    66   
2                           2.005291                    31   
3                           8.578610                   100   
4                         511.542003                    94   
5                         807.976982                     1   
6                           0.281718                    25   
7                          15.181170                   100   
8                         484.410284                    53   
9                           2.233107                    26   
10                          6.727216                    63   
11                          0.034049                    98   
12                       5292.453229                    41   
13                       2152.396706                     1   
14                         36.042065                   100   
15                         12.721894                   100   
16                         16.688814                   100   
17                        118.488829                    96   
18                          5.773988                    60   
19                          0.077429                    53   
20                          2.435483                    37   
21                         21.628371                    37   
22                       2001.021724                    89   
23                        131.419387                    17   
24                       1138.735917                    33   
25                        123.316414                    58   
26                          3.093593                    32   
27                       1925.587678                    61   
28                         13.653988                    35   
29                        140.017676                   100   

    Медиана времени до лучшей итерации  num_parents_mating  sol_per_pop   
0                             2.626016                 249          301  \
1                             2.682012                 160          209   
2                             4.757012                  44          305   
3                             7.380110                 131          131   
4                            15.260571                 217          217   
5                             0.120498                 376          376   
6                             4.395514                 324          402   
7                            24.639659                 290          290   
8                             3.973532                 116          116   
9                             6.713555                 118          403   
10                            6.328058                 121          121   
11                           29.788737                 383          494   
12                           24.994205                 180          398   
13                            7.704571                 318          338   
14                            7.062562                 104          104   
15                           31.646565                 367          367   
16                           17.585671                 221          221   
17                           13.846635                  67          268   
18                           17.758682                 314          470   
19                           10.715402                 240          496   
20                           14.984155                 430          477   
21                            1.084019                 117          117   
22                           20.326216                 299          299   
23                            1.670014                  93          197   
24                            3.100035                  11          187   
25                            5.276551                 215          215   
26                            9.975613                 3

In [3]:
df_summary.to_csv('pygad_shvefel.csv', index=False)

In [5]:
df_summary.describe().T

count         mean         std   
Медиана значения функции Швефеля     30.0   339.150882  980.411377  \
Мода лучшей итерации                 30.0    50.833333   34.562371   
Медиана времени до лучшей итерации   30.0    30.996559   39.417985   
num_parents_mating                   30.0   714.533333  557.298826   
sol_per_pop                          30.0  1457.833333  795.746064   
mutation_percent_genes               30.0    23.978463   13.316596   
random_mutation_min_val              30.0    -5.655595    2.891383   
random_mutation_max_val              30.0     4.982281    3.269902   
keep_parents                         30.0     0.437327    0.314965   
num_genes                            30.0    18.100000    7.087386   

                                           min         25%          50%   
Медиана значения функции Швефеля      0.004623    0.182056     4.333095  \
Мода лучшей итерации                  4.000000   18.500000    48.000000   
Медиана времени до лучшей итерации    1.090975    6.324268    14.740452   
num_parents_mating                  102.000000  247.250000   528.500000   
sol_per_pop                         109.000000  923.000000  1360.500000   
mutation_percent_genes                1.561154   13.279658    25.149923   
random_mutation_min_val              -9.794854   -8.808101    -5.086888   
random_mutation_max_val               0.022215    1.865843     4.595692   
keep_parents                          0.018777    0.120236     0.419638   
num_genes                             5.000000   14.250000    19.500000   

                                            75%          max  
Медиана значения функции Швефеля      98.254566  4564.869002  
Мода лучшей итерации                  91.250000   100.000000  
Медиана времени до лучшей итерации    36.734646   169.608371  
num_parents_mating                  1099.250000  1975.000000  
sol_per_pop                         2015.750000  2858.000000  
mutation_percent_genes                31.090669    49.527235  
random_mutation_min_val               -3.371041    -0.724696  
random_mutation_max_val                7.831038     9.650427  
keep_parents                           0.720067     0.962872  
num_genes                             23.000000    30.000000

In [6]:
df_rastrigin = pd.read_csv('pygad_rastrigin.csv')
df_rastrigin.describe().T

count         mean         std   
Медиана значения функции Растригина   30.0    20.472662   27.788651  \
Мода лучшей итерации                  30.0    62.866667   34.268447   
Медиана времени до лучшей итерации    30.0    27.429177   22.567384   
num_parents_mating                    30.0   780.966667  443.224352   
sol_per_pop                           30.0  1491.633333  828.606536   
num_genes                             30.0    19.533333    7.407980   
mutation_percent_genes                30.0    20.330379   11.666403   
random_mutation_min_val               30.0    -4.528009    2.896952   
random_mutation_max_val               30.0     4.436149    2.726303   
keep_parents                          30.0     0.510168    0.314860   

                                            min         25%          50%   
Медиана значения функции Растригина    0.000797    0.456978     6.688938  \
Мода лучшей итерации                   1.000000   33.000000    65.500000   
Медиана времени до лучшей итерации     0.054663   12.401746    22.614365   
num_parents_mating                   117.000000  362.750000   779.000000   
sol_per_pop                          117.000000  884.750000  1283.500000   
num_genes                              8.000000   13.250000    21.000000   
mutation_percent_genes                 3.581128   12.285763    16.225847   
random_mutation_min_val               -9.202380   -6.997890    -4.585747   
random_mutation_max_val                0.463489    2.013009     4.630504   
keep_parents                           0.023001    0.287804     0.518750   

                                             75%          max  
Медиана значения функции Растригина    32.833329   118.032329  
Мода лучшей итерации                   97.250000   100.000000  
Медиана времени до лучшей итерации     36.180500   107.584214  
num_parents_mating                   1122.000000  1599.000000  
sol_per_pop                          2310.750000  2897.000000  
num_genes                              25.500000    30.000000  
mutation_percent_genes                 25.866298    47.657515  
random_mutation_min_val                -1.740203    -0.175526  
random_mutation_max_val                 5.903222     9.631682  
keep_parents                            0.807236     0.981506